## Part 1

In [190]:
TEST_INFILE = "inputs/day_23_test_1.txt"
INFILE = "inputs/day_23_1.txt"

#with open(TEST_INFILE) as infile:
with open(INFILE) as infile:
    lines = infile.read().splitlines()

In [191]:
from enum import Enum


class Point:
    def __init__(self, row, col):
        self.row = row
        self.col = col

    def __repr__(self):
        return f"({self.row}, {self.col})"

    def __add__(self, other):
        return Point(self.row + other.row, self.col + other.col)

    def __radd__(self, other):
        return self + other
    
    def __eq__(self, other):
        return self.row == other.row and self.col == other.col
    
    def __lt__(self, other):
        return (self.row, self.col) < (other.row, other.col)

    def __hash__(self):
        return hash((self.row, self.col))
    

class Direction(Enum):
    UP = Point(-1, 0)
    DOWN = Point(1, 0)
    LEFT = Point(0, -1)
    RIGHT = Point(0, 1)

In [192]:
grid = [list(line) for line in lines]
START = Point(0, grid[0].index("."))
END   = Point(len(grid) - 1, grid[-1].index("."))
START, END

((0, 1), (140, 139))

In [193]:
def draw_path(path, grid=grid):
    for row_num in range(len(grid)):
        for col_num in range(len(grid[0])):
            if Point(row_num, col_num) in path:
                print("O", end="")
            else:
                print(grid[row_num][col_num], end="")
        print()

In [194]:
def get_neighbors(point, path=None, goal=END, grid=grid, debug=False) -> list[tuple[int, Point]]:
    if path is None:
        path = []

    path.append(point)

    if debug: print(f"Getting neighbors for {point} at dist {len(path) - 1}")

    slope_map = {
        "<": Direction.LEFT,
        ">": Direction.RIGHT,
        "^": Direction.UP,
        "v": Direction.DOWN,
    }

    neighbors = []
    for direction in Direction:
        neighbor = point + direction.value

        if neighbor == goal:
            if debug: print(f"Reached goal at {neighbor} in {len(path)} steps")
            neighbors.append((neighbor, path.copy()))
            continue

        if neighbor in path:
            continue

        if neighbor.row < 0 or neighbor.row >= len(grid):
            continue
        if neighbor.col < 0 or neighbor.col >= len(grid[0]):
            continue
        
        symbol = grid[neighbor.row][neighbor.col]
        if symbol == "#":
            continue

        if symbol in slope_map:
            next_neighbor = neighbor + slope_map[symbol].value
            # we can step onto a slope that takes us back to where we were,
            # so check that
            if next_neighbor == pos:
                continue
            else:
                neighbors.append((next_neighbor, path+[neighbor]))

        if symbol == ".":
            next_neighbors = get_neighbors(neighbor, path.copy(), grid=grid, debug=debug)
            neighbors.extend(next_neighbors)

    return neighbors

In [195]:
valid_paths = []
queue = [(START, None)]
while len(queue) > 0:
    pos, path = queue.pop(0)
    neighbors = get_neighbors(pos, path, debug=False)
    for neighbor in neighbors:
        if neighbor[0] == END:
            print(f"Found end at dist {len(neighbor[1]+[END])- 1} path {neighbor[1]+[END]}")
            valid_paths.append(neighbor[1]+[END])
        else:
            queue.append((neighbor[0], neighbor[1]))

Found end at dist 1918 path [(0, 1), (1, 1), (2, 1), (3, 1), (4, 1), (5, 1), (5, 2), (5, 3), (4, 3), (3, 3), (2, 3), (1, 3), (1, 4), (1, 5), (2, 5), (3, 5), (4, 5), (5, 5), (5, 6), (5, 7), (4, 7), (3, 7), (2, 7), (1, 7), (1, 8), (1, 9), (1, 10), (1, 11), (1, 12), (1, 13), (2, 13), (3, 13), (3, 12), (3, 11), (3, 10), (3, 9), (4, 9), (5, 9), (5, 10), (5, 11), (5, 12), (5, 13), (6, 13), (7, 13), (7, 14), (7, 15), (6, 15), (5, 15), (4, 15), (3, 15), (2, 15), (1, 15), (1, 16), (1, 17), (2, 17), (3, 17), (4, 17), (5, 17), (6, 17), (7, 17), (8, 17), (9, 17), (10, 17), (11, 17), (12, 17), (13, 17), (14, 17), (15, 17), (16, 17), (17, 17), (17, 16), (17, 15), (16, 15), (15, 15), (14, 15), (13, 15), (12, 15), (11, 15), (10, 15), (9, 15), (9, 14), (9, 13), (9, 12), (9, 11), (10, 11), (11, 11), (11, 12), (11, 13), (12, 13), (13, 13), (13, 12), (13, 11), (14, 11), (15, 11), (15, 10), (15, 9), (14, 9), (13, 9), (12, 9), (11, 9), (10, 9), (9, 9), (8, 9), (7, 9), (7, 8), (7, 7), (8, 7), (9, 7), (9, 6),

In [196]:
max(len(vp) - 1 for vp in valid_paths)

2074

In [197]:
draw_path(valid_paths[-1])

#O###########################################################################################################################################
#O#OOO#OOOOOOO#OOO#OOOOO#OOO#OOO#######OOO###OOO#OOO#OOOOOOO#OOO#OOO#OOO#OOO#OOO#OOO#OOO###OOO###OOO###...............#.....#...#######...###
#O#O#O#O#####O#O#O#O###O#O#O#O#O#######O#O###O#O#O#O#O#####O#O#O#O#O#O#O#O#O#O#O#O#O#O#O###O#O###O#O###.#############.#.###.#.#.#######.#.###
#O#O#O#O#OOOOO#O#O#OOO#O#O#OOO#OOO#OOOOO#OOO#O#O#O#O#OOOOO#OOO#O#O#O#O#O#O#O#O#OOO#OOO#OOOOO#O#OOO#OOO#.............#.#...#...#.......#.#...#
#O#O#O#O#O#####O#O###O#O#O#######O#O#######O#O#O#O#O#####O#####O#O#O#O#O#O#O#O###############O#O#####O#############.#.###.###########.#.###.#
#OOO#OOO#OOOOO#O#O###O#O#O#OOOOOOO#OOOOO#OOO#O#O#O#O#OOOOO#OOOOO#O#O#O#O#O#O#OOO#OOOOOOOOOOOOO#O#OOOOO#OOO#.......#.#.....#...........#.#...#
#############O#O#O###O#O#O#O###########O#O###O#O#O#O#O#v###O#####O#O#O#O#O#O###O#O#############O#O#####O#O#.#####.#.#######.###########.#.###
#...##

## Part 2

In [199]:
from collections import defaultdict

In [200]:
slope_map = {
    "<": Direction.LEFT,
    ">": Direction.RIGHT,
    "^": Direction.UP,
    "v": Direction.DOWN,
}
new_grid = [[r if r not in slope_map else "." for r in row ] for row in grid]

In [201]:
draw_path([], grid=new_grid)

#.###########################################################################################################################################
#.#...#.......#...#.....#...#...#######...###...#...#.......#...#...#...#...#...#...#...###...###...###...............#.....#...#######...###
#.#.#.#.#####.#.#.#.###.#.#.#.#.#######.#.###.#.#.#.#.#####.#.#.#.#.#.#.#.#.#.#.#.#.#.#.###.#.###.#.###.#############.#.###.#.#.#######.#.###
#.#.#.#.#.....#.#.#...#.#.#...#...#.....#...#.#.#.#.#.....#...#.#.#.#.#.#.#.#.#...#...#.....#.#...#...#.............#.#...#...#.......#.#...#
#.#.#.#.#.#####.#.###.#.#.#######.#.#######.#.#.#.#.#####.#####.#.#.#.#.#.#.#.###############.#.#####.#############.#.###.###########.#.###.#
#...#...#.....#.#.###.#.#.#.......#.....#...#.#.#.#.#.....#.....#.#.#.#.#.#.#...#.............#.#.....#...#.......#.#.....#...........#.#...#
#############.#.#.###.#.#.#.###########.#.###.#.#.#.#.#.###.#####.#.#.#.#.#.###.#.#############.#.#####.#.#.#####.#.#######.###########.#.###
#...##

In [202]:
def is_junction(pos, grid=new_grid):
    symbol = grid[pos.row][pos.col]
    if symbol != ".":
        return False

    neighbors = []
    for direction in Direction:
        neighbor = pos + direction.value
        if neighbor.row < 0 or neighbor.row >= len(grid):
            continue
        if neighbor.col < 0 or neighbor.col >= len(grid[0]):
            continue
        neighbor_symbol = grid[neighbor.row][neighbor.col]
        if neighbor_symbol == ".":
            neighbors.append(neighbor)

    return len(neighbors) > 2

In [203]:
junctions = []
for row_num in range(len(new_grid)):
    for col_num in range(len(new_grid[0])):
        if is_junction(Point(row_num, col_num)):
            junctions.append(Point(row_num, col_num))
len(junctions)

34

In [204]:
def get_valid_neighbors(pos, grid=new_grid):
    neighbors = []
    for direction in Direction:
        neighbor = pos + direction.value
        if neighbor.row < 0 or neighbor.row >= len(grid):
            continue
        if neighbor.col < 0 or neighbor.col >= len(grid[0]):
            continue
        symbol = grid[neighbor.row][neighbor.col]
        if symbol == "#":
            continue
        neighbors.append((direction, neighbor))
    return neighbors

In [205]:
def walk_until_junction_or_end(start, direction, junctions, grid=new_grid, debug=False):
    visited = [start]
    neighbor = start + direction.value
    if debug:
        print(f"Starting at neighbor {neighbor} in direction {direction}")
    if grid[neighbor.row][neighbor.col] == ".":
        visited.append(neighbor)
        while neighbor not in junctions and neighbor != END and neighbor != START:
            next_neighbors = get_valid_neighbors(neighbor, grid=grid)
            if debug:
                print(f"At {neighbor}, next neighbors: {next_neighbors}")
            next_neighbors = [n for n in next_neighbors if n[1] not in visited]
            if debug:
                print(f"Filtered next neighbors: {next_neighbors}")
            if len(next_neighbors) != 1:
                return None, None
            neighbor = next_neighbors[0][1]
            visited.append(neighbor)

    return len(visited) - 1, neighbor

In [206]:
# create our new, condensed graph
graph = defaultdict(dict)

queue = [START]
while len(queue) > 0:
    pos = queue.pop(0)
    neighbors = get_valid_neighbors(pos)
    for direction, neighbor in neighbors:
        #print(f"From {pos}, can go {direction} to {neighbor}")
        steps, junction = walk_until_junction_or_end(pos, direction, junctions)
        if steps is not None:
            #print(f"\tWalked {steps} steps to {junction}")
            if junction not in graph:
                queue.append(junction)
            graph[pos][junction] = steps
            graph[junction][pos] = steps

In [207]:
len(graph.keys())

36

In [208]:
graph

defaultdict(dict,
            {(0, 1): {(7, 17): 59},
             (7, 17): {(0, 1): 59, (43, 5): 228, (19, 35): 162},
             (43, 5): {(7, 17): 228, (61, 9): 102, (29, 35): 180},
             (19, 35): {(7, 17): 162, (29, 35): 34, (5, 55): 174},
             (61, 9): {(43, 5): 102, (75, 17): 138, (67, 29): 102},
             (29, 35): {(43, 5): 180,
              (19, 35): 34,
              (67, 29): 252,
              (29, 63): 224},
             (5, 55): {(19, 35): 174, (29, 63): 128, (9, 77): 138},
             (75, 17): {(61, 9): 138, (99, 7): 138, (81, 33): 94},
             (67, 29): {(61, 9): 102,
              (29, 35): 252,
              (81, 33): 74,
              (59, 67): 286},
             (29, 63): {(29, 35): 224,
              (5, 55): 128,
              (59, 67): 178,
              (31, 75): 34},
             (9, 77): {(5, 55): 138, (31, 75): 72, (17, 107): 298},
             (99, 7): {(75, 17): 138, (131, 33): 474, (113, 33): 156},
             (81, 33): {(75, 1

In [209]:
def get_paths_to_end(start, end=END, path=None, indent=0, debug=False):
    tab = "\t" * indent
    if debug: print(f"{tab}Getting paths from {start} with current path {path}")
    if path is None:
        path = [(0, start)]

    if debug: print(f"{tab}Neighbors: {graph[start]}")
    results = []
    for neighbor, dist in graph[start].items():
        if debug: print(f"{tab} Looking at neighbor {neighbor} at dist {dist}")
        if neighbor in [p[1] for p in path]:
            if debug: print(f"{tab} Already visited {neighbor}, skipping")
            continue

        if neighbor == end:
            if debug: print(f"{tab}Reached end at {neighbor} in {len(path)} steps")
            results.extend([path + [(dist, end)]])
        else:
            results.extend(get_paths_to_end(neighbor, end=end, path=path + [(dist, neighbor)], indent=indent + 1, debug=debug))

    if debug: print(f"{tab}Returning results {results}")
    return results

In [210]:
paths = get_paths_to_end(START, path=None, debug=False)

In [211]:
len(paths)

1262816

In [213]:
max(sum(p[0] for p in path) for path in paths)

6494